### This is a new version of MLEAP scripts, started in late Aug 2022.
It will combine IProject_MLEAP_ANN and IP_MLEAP script, while improving them.

#### Outline

1. Load libraries and data.
2. pEDA. Look at feature distribution, fix them if they do not look right.
3. Train-test split. Most likely couple years into test set. 2015-2018?. Impute missing values.
4. Transform numerical features, add ohe for inds.
5. Fit classic models: ols as a baseline, then xgb.
6. Fit DL.


In [1]:
# 0. Import libraries #

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import os, time, math, re, warnings, random, gc, dill, optuna, pickle
import statsmodels.api as sm
from random import sample

from sklearn.model_selection import train_test_split, KFold, PredefinedSplit
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from sklearn.linear_model import LinearRegression, Lasso, Ridge, ElasticNetCV
from sklearn.preprocessing import LabelBinarizer, LabelEncoder, OrdinalEncoder, OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer, make_column_transformer
from sklearn.metrics import r2_score, mean_absolute_error
from sklearn.inspection import permutation_importance
from category_encoders import MEstimateEncoder
from xgboost import XGBRegressor

import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Activation, Flatten, BatchNormalization
from tensorflow.keras.callbacks import EarlyStopping

plt.style.use('seaborn-white')
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', 110)
gc.enable()

In [2]:
### target encoding ###
# source: https://www.kaggle.com/code/ryanholbrook/feature-engineering-for-house-prices/notebook

class CrossFoldEncoder:
    def __init__(self, encoder, **kwargs):
        self.encoder_ = encoder
        self.kwargs_ = kwargs  # keyword arguments for the encoder
        self.cv_ = KFold(n_splits=4)

    # Fit an encoder on one split and transform the feature on the
    # other. Iterating over the splits in all folds gives a complete
    # transformation. We also now have one trained encoder on each
    # fold.
    def fit_transform(self, X, y, cols):
        self.fitted_encoders_ = []
        self.cols_ = cols
        X_encoded = []
        for idx_encode, idx_train in self.cv_.split(X):
            fitted_encoder = self.encoder_(cols=cols, **self.kwargs_)
            fitted_encoder.fit(
                X.iloc[idx_encode, :], y.iloc[idx_encode],
            )
            X_encoded.append(fitted_encoder.transform(X.iloc[idx_train, :])[cols])
            self.fitted_encoders_.append(fitted_encoder)
        X_encoded = pd.concat(X_encoded)
        X_encoded.columns = [name + "_encoded" for name in X_encoded.columns]
        return X_encoded

    # To transform the test data, average the encodings learned from
    # each fold.
    def transform(self, X):
        from functools import reduce

        X_encoded_list = []
        for fitted_encoder in self.fitted_encoders_:
            X_encoded = fitted_encoder.transform(X)
            X_encoded_list.append(X_encoded[self.cols_])
        X_encoded = reduce(
            lambda x, y: x.add(y, fill_value=0), X_encoded_list
        ) / len(X_encoded_list)
        X_encoded.columns = [name + "_encoded" for name in X_encoded.columns]
        return X_encoded

In [3]:
# Detect TPU, return appropriate distribution strategy
try:
    tpu = tf.distribute.cluster_resolver.TPUClusterResolver() 
    print('Running on TPU ', tpu.master())
except ValueError:
    tpu = None

if tpu:
    tf.config.experimental_connect_to_cluster(tpu)
    tf.tpu.experimental.initialize_tpu_system(tpu)
    strategy = tf.distribute.experimental.TPUStrategy(tpu)
else:
    strategy = tf.distribute.get_strategy() 

print("REPLICAS: ", strategy.num_replicas_in_sync)

REPLICAS:  1


In [4]:
#min_prd_list = [450, 550]
min_prd_list = range(100, 691, 10)

windows_width = 3*12
cv_regularizer=1
optuna_trials = 50
time0 = time.time()

results = pd.DataFrame(columns = ['min_prd', 'xgbf_train', 'xgbf_val', 'xgbf_test', 
                                  'xgbgs_train', 'xgbgs_val', 'xgbgs_test', 
                                  'xgbo1_train', 'xgbo1_val', 'xgbo1_test',
                                  'xgbo2_train', 'xgbo2_val', 'xgbo2_test',
                                 'xgbonr_train', 'xgbonr_val', 'xgbonr_test'])
results.min_prd = min_prd_list

for min_prd in min_prd_list:

    with open('../input/kaggle-46pkl/IMLEAP_v4.pkl', 'rb') as pickled_one:
        df = pickle.load(pickled_one)
    df = df[df.prd.isin(range(min_prd-1, min_prd+windows_width+3))]
    df_cnt = df.count()
    empty_cols = list(df_cnt[df_cnt<int(df.shape[0]/2)].index)
    df.drop(columns=empty_cols, inplace=True)
    #display(df.shape, df.head(), df.year.describe(), df.count())

    df = df[(df.RET>-50)&(df.RET<75)]
    meanret = df.groupby('prd').RET.mean().to_frame().reset_index().rename(columns={'RET':'mRET'})
    df = pd.merge(df, meanret, on='prd', how='left')
    df.RET = df.RET-df.mRET
    df.drop(columns='mRET', inplace=True)

    features_miss_dummies = ['amhd', 'BAspr']
    for col in features_miss_dummies:
        if col in df.columns:
            df[col+'_miss'] = df[col].isnull().astype(int)

    temp_cols = ['PERMNO', 'year', 'prd']
    df.reset_index(inplace=True, drop=True)
    X = df.copy()
    y = X.pop('RET')

    train_indx = X.prd<(min_prd+windows_width-1)
    val_indx = X.prd==(min_prd+windows_width-1)
    val_indx_extra = X.prd==(min_prd+windows_width+1)
    test_indx = X.prd==(min_prd+windows_width)

    X_train = X[train_indx]
    X_val = X[val_indx]
    X_val_extra = X[val_indx_extra]
    X_test = X[test_indx]
    y_train = y[train_indx]
    y_val = y[val_indx]
    y_val_extra = y[val_indx_extra]
    y_test = y[test_indx]

    #display(X_train.head(3), X_train.tail(3), y_train.head(3), y_train.tail(3))
    display(X_train.shape, X_val.shape, X_test.shape, X_train.prd.describe(), X_val.prd.describe(), X_test.prd.describe())

    X_train.drop(columns=temp_cols, inplace=True)
    X_val.drop(columns=temp_cols, inplace=True)
    X_val_extra.drop(columns=temp_cols, inplace=True)
    X_test.drop(columns=temp_cols, inplace=True)

    #display(X_train.tail())
    col_cat = ['ind']
    col_num = [x for x in X_train.columns if x not in col_cat]
    for col in col_num:
        X_train[col] = X_train[col].fillna(X_train[col].median())
        X_val[col] = X_val[col].fillna(X_train[col].median())
        X_val_extra[col] = X_val_extra[col].fillna(X_train[col].median())
        X_test[col] = X_test[col].fillna(X_train[col].median())
    for col in col_cat:
        X_train[col] = X_train[col].fillna(value=-1000)
        X_val[col] = X_val[col].fillna(value=-1000)
        X_val_extra[col] = X_val_extra[col].fillna(value=-1000)
        X_test[col] = X_test[col].fillna(value=-1000)

    #display(X_train.tail())
    feature_transformer = ColumnTransformer([('num', StandardScaler(), col_num),
                                            ("cat", OneHotEncoder(sparse = False, handle_unknown="ignore", drop='if_binary'), col_cat)], 
                                            remainder="passthrough")

    print('Number of features before transformation: ', X_train.shape)
    train_index, val_index, val_index_extra, test_index = X_train.index, X_val.index, X_val_extra.index, X_test.index
    X_train = pd.DataFrame(feature_transformer.fit_transform(X_train), columns=feature_transformer.get_feature_names_out())
    X_val = pd.DataFrame(feature_transformer.transform(X_val), columns=feature_transformer.get_feature_names_out())
    X_val_extra = pd.DataFrame(feature_transformer.transform(X_val_extra), columns=feature_transformer.get_feature_names_out())
    X_test = pd.DataFrame(feature_transformer.transform(X_test), columns=feature_transformer.get_feature_names_out())
    print('time to do feature proprocessing: ')
    print('Number of features after transformation: ', X_train.shape, X_val.shape, X_val_extra.shape, X_test.shape)
    X_train.index = train_index
    X_val.index = val_index
    X_val_extra.index = val_index_extra
    X_test.index = test_index
    #display(X_train.tail())

    X = pd.concat([X_train, X_val])
    y = pd.concat([y_train, y_val])
    #display(X,y)

    X_ = pd.concat([X_train, X_val, X_val_extra])
    y_ = pd.concat([y_train, y_val, y_val_extra])
    #display(X,y, X_,y_)

    print('mae of a constant model', mean_absolute_error(df.RET, np.ones(df.shape[0])*(df.RET.mean())))
    print('R2 of a constant model', r2_score(df.RET, np.ones(df.shape[0])*(df.RET.mean())))

    xgb1 = XGBRegressor(tree_method = 'gpu_hist', n_estimators=400, max_depth=4, eta=0.02, colsample_bytree=0.4, subsample=0.6)
    xgb1.fit(X_train, y_train)
    print('XGB train:', mean_absolute_error(y_train, xgb1.predict(X_train)), r2_score(y_train, xgb1.predict(X_train)))
    print('XGB val:', mean_absolute_error(y_val, xgb1.predict(X_val)), r2_score(y_val, xgb1.predict(X_val)))
    print('XGB val extra:', mean_absolute_error(y_val_extra, xgb1.predict(X_val_extra)), r2_score(y_val_extra, xgb1.predict(X_val_extra)))
    print('XGB test:', mean_absolute_error(y_test, xgb1.predict(X_test)), r2_score(y_test, xgb1.predict(X_test)))

    results.loc[results.min_prd==min_prd,'xgbf_train':'xgbf_test'] = \
    [r2_score(y_train, xgb1.predict(X_train)), 
    r2_score(y_val, xgb1.predict(X_val)),
    r2_score(y_test, xgb1.predict(X_test))]

    time1 = time.time()

    # Create a list where train data indices are -1 and validation data indices are 0
    split_index = [-1 if x in X_train.index else 0 for x in X.index]
    pds = PredefinedSplit(test_fold = split_index)

    xgb = XGBRegressor(tree_method = 'gpu_hist')
    param_grid = {'n_estimators':[400, 600, 800], 'max_depth':[2,3,4], 'eta':[0.006, 0.012, 0.02], 
                  'subsample':[0.6], 'colsample_bytree':[0.6]}
    xgbgs = GridSearchCV(estimator = xgb, cv=pds, param_grid=param_grid)

    # Fit with all data
    xgbgs.fit(X_, y_)

    print('XGB', xgbgs.best_params_, xgbgs.best_score_, time.time()-time1)
    print('XGB train:', mean_absolute_error(y_train, xgbgs.predict(X_train)), r2_score(y_train, xgbgs.predict(X_train)))
    print('XGB validation:', mean_absolute_error(y_val, xgbgs.predict(X_val)), r2_score(y_val, xgbgs.predict(X_val)))
    print('XGB validation extra:', mean_absolute_error(y_val_extra, xgbgs.predict(X_val_extra)), r2_score(y_val_extra, xgbgs.predict(X_val_extra)))
    print('XGB test:', mean_absolute_error(y_test, xgbgs.predict(X_test)), r2_score(y_test, xgbgs.predict(X_test)))

    results.loc[results.min_prd==min_prd,'xgbgs_train':'xgbgs_test'] = \
    [r2_score(y_train, xgbgs.predict(X_train)), 
    r2_score(y_val, xgbgs.predict(X_val)),
    r2_score(y_test, xgbgs.predict(X_test))]

    time1 = time.time()
    def objective(trial, cv_runs=1, n_splits=2, n_jobs=-1):

        params = {
        "tree_method": 'gpu_hist',
        "verbosity": 0,  # 0 (silent) - 3 (debug)
        "n_estimators": trial.suggest_int("n_estimators", 500, 1000),
        "max_depth": trial.suggest_int("max_depth", 2, 5),
        "learning_rate": trial.suggest_uniform("learning_rate", 0.0005, 0.03),
        "colsample_bytree": trial.suggest_uniform("colsample_bytree", 0.05, 0.95),
        "subsample": trial.suggest_uniform("subsample", 0.1, 0.95),
        "alpha": trial.suggest_loguniform("alpha", 0.1, 50.0),
        "lambda": trial.suggest_loguniform("lambda", 0.1, 500.0),
        "gamma": trial.suggest_loguniform("gamma", 1e-10, 100.0),
        "min_child_weight": trial.suggest_loguniform("min_child_weight", 0.1, 100)    }

        model = XGBRegressor(**params, njobs=-1)
        model.fit(X_train, y_train, eval_set=[(X_val, y_val)], early_stopping_rounds=50, verbose = False)

        score_train = r2_score(y_train, model.predict(X_train))
        score_val = r2_score(y_val, model.predict(X_val))
        score_val_extra = r2_score(y_val_extra, model.predict(X_val_extra)) 
        score_val = (score_val+score_val_extra)/2
        overfit = np.abs(score_train-score_val)

        return score_val-cv_regularizer*overfit


    study = optuna.create_study(direction="maximize")
    study.optimize(objective, n_trials=optuna_trials)
    print('Total time for hypermarameter optimization ', time.time()-time1)
    hp = study.best_params
    for key, value in hp.items():
        print(f"{key:>20s} : {value}")
    print(f"{'best objective value':>20s} : {study.best_value}")
    optuna_hyperpars = study.best_params
    optuna_hyperpars['tree_method']='gpu_hist'
    optuna_xgb = XGBRegressor(**optuna_hyperpars)
    optuna_xgb.fit(X, y)
    print('Optuna XGB train: \n', 
          mean_absolute_error(y_train, optuna_xgb.predict(X_train)), r2_score(y_train, optuna_xgb.predict(X_train)), '\nvalidation \n',
          mean_absolute_error(y_val, optuna_xgb.predict(X_val)), r2_score(y_val, optuna_xgb.predict(X_val)),
          mean_absolute_error(y_val_extra, optuna_xgb.predict(X_val_extra)), r2_score(y_val_extra, optuna_xgb.predict(X_val_extra)), '\ntest \n',
          mean_absolute_error(y_test, optuna_xgb.predict(X_test)), r2_score(y_test, optuna_xgb.predict(X_test)))

    results.loc[results.min_prd==min_prd,'xgbo1_train':'xgbo1_test'] = \
    [r2_score(y_train, optuna_xgb.predict(X_train)), 
    r2_score(y_val, optuna_xgb.predict(X_val)),
    r2_score(y_test, optuna_xgb.predict(X_test))]

    
    cv_regularizer = 0.3
    
    time1 = time.time()
    def objective(trial, cv_runs=1, n_splits=2, n_jobs=-1):

        params = {
        "tree_method": 'gpu_hist',
        "verbosity": 0,  # 0 (silent) - 3 (debug)
        "n_estimators": trial.suggest_int("n_estimators", 500, 1000),
        "max_depth": trial.suggest_int("max_depth", 2, 5),
        "learning_rate": trial.suggest_uniform("learning_rate", 0.0005, 0.03),
        "colsample_bytree": trial.suggest_uniform("colsample_bytree", 0.05, 0.95),
        "subsample": trial.suggest_uniform("subsample", 0.1, 0.95),
        "alpha": trial.suggest_loguniform("alpha", 0.1, 50.0),
        "lambda": trial.suggest_loguniform("lambda", 0.1, 500.0),
        "gamma": trial.suggest_loguniform("gamma", 1e-10, 100.0),
        "min_child_weight": trial.suggest_loguniform("min_child_weight", 0.1, 100)    }

        model = XGBRegressor(**params, njobs=-1)
        model.fit(X_train, y_train, eval_set=[(X_val, y_val)], early_stopping_rounds=50, verbose = False)

        score_train = r2_score(y_train, model.predict(X_train))
        score_val = r2_score(y_val, model.predict(X_val))
        score_val_extra = r2_score(y_val_extra, model.predict(X_val_extra)) 
        score_val = (score_val+score_val_extra)/2
        overfit = np.abs(score_train-score_val)

        return score_val-cv_regularizer*overfit


    study = optuna.create_study(direction="maximize")
    study.optimize(objective, n_trials=optuna_trials)
    print('Total time for hypermarameter optimization ', time.time()-time1)
    hp = study.best_params
    for key, value in hp.items():
        print(f"{key:>20s} : {value}")
    print(f"{'best objective value':>20s} : {study.best_value}")
    optuna_hyperpars = study.best_params
    optuna_hyperpars['tree_method']='gpu_hist'
    optuna_xgb = XGBRegressor(**optuna_hyperpars)
    optuna_xgb.fit(X, y)
    print('Optuna XGB train: \n', 
          mean_absolute_error(y_train, optuna_xgb.predict(X_train)), r2_score(y_train, optuna_xgb.predict(X_train)), '\nvalidation \n',
          mean_absolute_error(y_val, optuna_xgb.predict(X_val)), r2_score(y_val, optuna_xgb.predict(X_val)),
          mean_absolute_error(y_val_extra, optuna_xgb.predict(X_val_extra)), r2_score(y_val_extra, optuna_xgb.predict(X_val_extra)), '\ntest \n',
          mean_absolute_error(y_test, optuna_xgb.predict(X_test)), r2_score(y_test, optuna_xgb.predict(X_test)))

    results.loc[results.min_prd==min_prd,'xgbo2_train':'xgbo2_test'] = \
    [r2_score(y_train, optuna_xgb.predict(X_train)), 
    r2_score(y_val, optuna_xgb.predict(X_val)),
    r2_score(y_test, optuna_xgb.predict(X_test))]
    
    
    
    
    
    # now w/o regularization    
    time1 = time.time()
    def objective(trial, cv_runs=1, n_splits=2, n_jobs=-1):

        params = {
        "tree_method": 'gpu_hist',
        "verbosity": 0,  # 0 (silent) - 3 (debug)
        "n_estimators": trial.suggest_int("n_estimators", 500, 1000),
        "max_depth": trial.suggest_int("max_depth", 2, 5),
        "learning_rate": trial.suggest_uniform("learning_rate", 0.0005, 0.03),
        "colsample_bytree": trial.suggest_uniform("colsample_bytree", 0.05, 0.95),
        "subsample": trial.suggest_uniform("subsample", 0.1, 0.95),
        "alpha": trial.suggest_loguniform("alpha", 0.1, 50.0),
        "lambda": trial.suggest_loguniform("lambda", 0.1, 500.0),
        "gamma": trial.suggest_loguniform("gamma", 1e-10, 100.0),
        "min_child_weight": trial.suggest_loguniform("min_child_weight", 0.1, 100)    }

        model = XGBRegressor(**params, njobs=-1)
        model.fit(X_train, y_train, eval_set=[(X_val, y_val)], early_stopping_rounds=50, verbose = False)

        score_val = r2_score(y_val, model.predict(X_val))
        score_val_extra = r2_score(y_val_extra, model.predict(X_val_extra)) 
        score_val = (score_val+score_val_extra)/2

        return score_val


    study = optuna.create_study(direction="maximize")
    study.optimize(objective, n_trials=optuna_trials)
    print('Total time for hypermarameter optimization ', time.time()-time1)
    hp = study.best_params
    for key, value in hp.items():
        print(f"{key:>20s} : {value}")
    print(f"{'best objective value':>20s} : {study.best_value}")
    optuna_hyperpars = study.best_params
    optuna_hyperpars['tree_method']='gpu_hist'
    optuna_xgb = XGBRegressor(**optuna_hyperpars)
    optuna_xgb.fit(X, y)
    print('Optuna no regularization XGB train: \n', 
          mean_absolute_error(y_train, optuna_xgb.predict(X_train)), r2_score(y_train, optuna_xgb.predict(X_train)), '\nvalidation \n',
          mean_absolute_error(y_val, optuna_xgb.predict(X_val)), r2_score(y_val, optuna_xgb.predict(X_val)),
          mean_absolute_error(y_val_extra, optuna_xgb.predict(X_val_extra)), r2_score(y_val_extra, optuna_xgb.predict(X_val_extra)), '\ntest \n',
          mean_absolute_error(y_test, optuna_xgb.predict(X_test)), r2_score(y_test, optuna_xgb.predict(X_test)))

    results.loc[results.min_prd==min_prd,'xgbonr_train':'xgbonr_test'] = \
    [r2_score(y_train, optuna_xgb.predict(X_train)), 
    r2_score(y_val, optuna_xgb.predict(X_val)),
    r2_score(y_test, optuna_xgb.predict(X_test))]

    display(results)

(28169, 41)

(1079, 41)

(1054, 41)

count    28169.000000
mean       117.285988
std         10.355883
min         99.000000
25%        108.000000
50%        118.000000
75%        126.000000
max        134.000000
Name: prd, dtype: float64

count    1079.0
mean      135.0
std         0.0
min       135.0
25%       135.0
50%       135.0
75%       135.0
max       135.0
Name: prd, dtype: float64

...

[I 2022-08-27 23:09:35,807] A new study created in memory with name: no-name-7d8d6ff7-6e49-45cd-9656-e4a1cfe1a520
[I 2022-08-27 23:09:37,204] Trial 0 finished with value: 0.0037026782499559375 and parameters: {'n_estimators': 681, 'max_depth': 5, 'learning_rate': 0.00498005602252013, 'colsample_bytree': 0.24649254469207504, 'subsample': 0.11728689053679592, 'alpha': 41.41409896645164, 'lambda': 0.1781452105968804, 'gamma': 1.1553477874084212e-08, 'min_child_weight': 8.083988131639844}. Best is trial 0 with value: 0.0037026782499559375.
[I 2022-08-27 23:09:37,900] Trial 1 finished with value: 0.005530354828738554 and parameters: {'n_estimators': 697, 'max_depth': 3, 'learning_rate': 0.014953948864520382, 'colsample_bytree': 0.5557849752001643, 'subsample': 0.8267279701538593, 'alpha': 0.48981754274122097, 'lambda': 17.743188890219816, 'gamma': 3.1506648767032464e-06, 'min_child_weight': 83.15598009544615}. Best is trial 1 with value: 0.005530354828738554.
[I 2022-08-27 23:09:38,464] Tri

Total time for hypermarameter optimization  38.674500703811646
        n_estimators : 974
           max_depth : 2
       learning_rate : 0.013659041020884026
    colsample_bytree : 0.46437747745414804
           subsample : 0.31907252362214733
               alpha : 2.7210639110490535
              lambda : 271.8181101206672
               gamma : 0.010213308099701123
    min_child_weight : 9.36688816851511
best objective value : 0.007749933369763801
Optuna XGB train: 
 7.850822498076143 0.016532022916426414 
validation 
 6.61606936915541 0.013987966006175134 9.715891933215918 0.009360003567079556 
test 
 8.090683107874204 -0.005729314254533602


[I 2022-08-27 23:10:16,852] A new study created in memory with name: no-name-51b42d75-3d17-4c13-8132-9fe1e9e1751d
[I 2022-08-27 23:10:17,727] Trial 0 finished with value: 0.007817049718741254 and parameters: {'n_estimators': 871, 'max_depth': 2, 'learning_rate': 0.010943394754858008, 'colsample_bytree': 0.20445962293682374, 'subsample': 0.6683339716007065, 'alpha': 7.030748560200207, 'lambda': 176.1815107114019, 'gamma': 6.810187119982539e-07, 'min_child_weight': 24.9766986286849}. Best is trial 0 with value: 0.007817049718741254.
[I 2022-08-27 23:10:18,338] Trial 1 finished with value: 0.008129276238143357 and parameters: {'n_estimators': 658, 'max_depth': 5, 'learning_rate': 0.02499540221172399, 'colsample_bytree': 0.6646603209440787, 'subsample': 0.9110804464282936, 'alpha': 0.1489634782352784, 'lambda': 0.5872102291153535, 'gamma': 92.90385711884296, 'min_child_weight': 42.25793271755925}. Best is trial 1 with value: 0.008129276238143357.
[I 2022-08-27 23:10:18,762] Trial 2 finishe

Total time for hypermarameter optimization  40.52826690673828
        n_estimators : 922
           max_depth : 5
       learning_rate : 0.02200461990417464
    colsample_bytree : 0.18931044516200116
           subsample : 0.8983517225544794
               alpha : 49.017712168710624
              lambda : 0.13250919970875813
               gamma : 97.80080209029472
    min_child_weight : 21.309075388484466
best objective value : 0.010848663638838962
Optuna no regularization XGB train: 
 7.406473794644269 0.15955647785944393 
validation 
 6.2823521145905845 0.137699349014341 9.76658887191795 -0.0045441100722682926 
test 
 8.127784871596363 -0.013704356725475098


min_prd xgbf_train  xgbf_val xgbf_test xgbgs_train xgbgs_val xgbgs_test  \
0       100   0.099349 -0.003078 -0.042215    0.071155  0.059896  -0.023333   
1       110    0.09642 -0.024177   0.07694    0.044377  0.044562   0.064861   
2       120    0.09447  0.000334 -0.072939    0.044981  0.049467  -0.005743   
3       130   0.089606 -0.077258 -0.025995    0.015769  0.024445   0.004396   
4       140   0.079871  0.011749  0.031551    0.028158  0.023193   0.026371   
5       150   0.071204 -0.000161   0.01667    0.018317  0.016107   0.021498   
6       160   0.076594  0.049089  0.020355    0.114539  0.178917   0.019401   
7       170   0.074207 -0.006419  -0.00893    0.020759  0.005999   0.006901   
8       180   0.066243 -0.006079 -0.063589    0.020394  0.018005   0.003369   
9       190   0.069192  0.014459  0.013903    0.036827  0.043467   0.011792   
10      200   0.061512  0.008185  0.012473    0.096316  0.066212   0.008146   
11      210   0.054429  0.012006 -0.040438    0.024746  0.023663  -0.041929   
12      220   0.050578 -0.009155  0.003191    0.047805  0.022831   0.002471   
13      230   0.047724  0.002158  0.006554    0.035125  0.032208   0.008102   
14      240   0.047725  0.007272 -0.018707    0.077249  0.072814  -0.007266   
15      250   0.045741  0.006388 -0.005746    0.052305  0.066746   0.011374   
16      260   0.048274  0.039091  0.000284    0.054332  0.107294  -0.006535   
17      270   0.051839   0.01363  0.002825    0.032895  0.057244   0.009541   
18      280   0.056143  0.039569  0.013484    0.053483  0.098232    0.00659   
19      290   0.056558  0.018069  0.013477    0.025016  0.037646   0.020037   
20      300   0.057807  0.016672  0.000092    0.029723  0.035965   0.001072   
21      310   0.054427 -0.010972 -0.019696    0.015449 -0.001974  -0.005921   
22      320   0.047415  0.016685  0.005268    0.053188  0.096072  -0.002937   
23      330   0.045697  0.017697  0.019648    0.017961  0.033121    0.02515   
24      340   0.045888  0.021616  0.017732    0.034678  0.047366    0.01972   
25      350   0.046708    0.0213 -0.008795    0.046876  0.063495  -0.008645   
26      360   0.043983 -0.003061 -0.013485     0.02085  0.019719  -0.003817   
27      370   0.042501 -0.010907 -0.044916     0.04698  0.061389  -0.026002   
28      380   0.038704  0.014032  0.010633    0.036917  0.045396   0.012084   
29      390   0.038673  0.010581 -0.001659    0.039633  0.044377   0.000455   
30      400   0.040179  0.001551  0.004976    0.008676  0.010041   0.004496   
31      410   0.043489  0.013472  0.009085    0.070415  0.067326   0.014161   
32      420   0.041565 -0.001777  0.000869     0.00805  0.002289   0.000376   
33      430   0.042998 -0.006748  0.010326    0.024572  0.013089   0.015851   
34      440   0.041413  0.024514  0.017073    0.016278  0.034469   0.016894   
35      450   0.040478   -0.0114  0.000818    0.008984  0.010042    0.00815   
36      460   0.040323 -0.012433  0.002331    0.009622 -0.002945   0.003763   
37      470   0.039487  0.006875  0.006563    0.024344  0.064466  -0.020421   
38      480   0.041835   0.02849 -0.012097    0.018711  0.047383  -0.011722   
39      490   0.043434  0.011934 -0.002548     0.02232  0.031361   0.008431   
40      500   0.047328 -0.039274  0.077507    0.013421 -0.018604   0.046965   
41      510   0.051179   0.01092 -0.005847     0.08036  0.078548  -0.003326   
42      520   0.047858  0.032809 -0.006357    0.079084  0.091178  -0.014292   
43      530   0.046208 -0.009664  0.006593    0.011119   0.00384   0.008529   
44      540   0.047182  0.013875  0.017289    0.044065  0.037766   0.017505   
45      550   0.050095  -0.01019 -0.000978    0.023161  0.005404   0.000102   
46      560   0.048452  0.021626   0.01573    0.056044  0.051912   0.014923   
47      570    0.04822  0.006095 -0.011438    0.007742  0.018289  -0.009635   
48      580    0.05188 -0.017829   0.00466    0.007464  0.016465   0.009015   
49      590    0.05108 -0.026478 -0.032363    0.008295

In [5]:
print(results.iloc[:,1:].mean())
# cv_regularizer = 0.5
# optuna_trials = 80
print(time.time()-time0)

xgbf_train      0.055751
xgbf_val        0.002104
xgbf_test      -0.002258
xgbgs_train     0.034514
xgbgs_val       0.038115
xgbgs_test      0.004934
xgbo1_train     0.043007
xgbo1_val       0.051157
xgbo1_test      0.000564
xgbo2_train     0.037701
xgbo2_val       0.044234
xgbo2_test      0.000472
xgbonr_train    0.069810
xgbonr_val      0.078395
xgbonr_test    -0.000842
dtype: float64
14098.840530395508


In [6]:
results.to_csv('kp103_temp_xgb.csv')

# in the first run, gs performed best with r2 of 1.1 vs 0.7% for optuna with cv_reg=0.2 vs 0.5% for simple xgb.

In [7]:
# general point:
# compared to NN, xgb is harder to regularize
# in NN, you can simply shrink coefficient towards constant prediction.
# in xgb, you can not do that. the only way to regularize is via hyperparameters.
# in other words, by tweaking hyperpars, in NN you can approach R^2=0.0 prediction from a constant model arbitrarily close
# in xgb, you can not do that.
# by setting eta as low as 0.1% you can bring r2 down to 0.1%, but lowering eta further actyally increases abs(r2).